<a href="https://colab.research.google.com/github/hasmira0105/Tugas-Juwels/blob/main/Search_Engine_Sederhana.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Buatlah program search engine sederhana berdasarkan kolom 'content' untuk dataset berikut : https://raw.githubusercontent.com/zayedrais/DocumentSearchEngine/master/data/newsgroups.json


Note : Lakukan preprocessing terlebih dahulu (Stopword, Stemming, Lemmatize, dan juga penghilangan character tak berguna)

In [1]:
import numpy as np
import pandas as pd
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

import re
from nltk.corpus import stopwords
from nltk import word_tokenize
from nltk.stem import SnowballStemmer

In [2]:
import nltk
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [3]:
data = pd.read_json('https://raw.githubusercontent.com/zayedrais/DocumentSearchEngine/master/data/newsgroups.json')
data.head()

content  ...           target_names
0  From: lerxst@wam.umd.edu (where's my thing)\nS...  ...              rec.autos
1  From: guykuo@carson.u.washington.edu (Guy Kuo)...  ...  comp.sys.mac.hardware
2  From: twillis@ec.ecn.purdue.edu (Thomas E Will...  ...  comp.sys.mac.hardware
3  From: jgreen@amber (Joe Green)\nSubject: Re: W...  ...          comp.graphics
4  From: jcm@head-cfa.harvard.edu (Jonathan McDow...  ...              sci.space

[5 rows x 3 columns]

In [4]:
texts = data['content'].to_list()
texts

["From: lerxst@wam.umd.edu (where's my thing)\nSubject: WHAT car is this!?\nNntp-Posting-Host: rac3.wam.umd.edu\nOrganization: University of Maryland, College Park\nLines: 15\n\n I was wondering if anyone out there could enlighten me on this car I saw\nthe other day. It was a 2-door sports car, looked to be from the late 60s/\nearly 70s. It was called a Bricklin. The doors were really small. In addition,\nthe front bumper was separate from the rest of the body. This is \nall I know. If anyone can tellme a model name, engine specs, years\nof production, where this car is made, history, or whatever info you\nhave on this funky looking car, please e-mail.\n\nThanks,\n- IL\n   ---- brought to you by your neighborhood Lerxst ----\n\n\n\n\n",
 "From: guykuo@carson.u.washington.edu (Guy Kuo)\nSubject: SI Clock Poll - Final Call\nSummary: Final call for SI clock reports\nKeywords: SI,acceleration,clock,upgrade\nArticle-I.D.: shelley.1qvfo9INNc3s\nOrganization: University of Washington\nLines: 

In [5]:
# Menghilangkan email dengan regular expression
email_pattern = re.compile(r'[\w._%+-]+@[\w\.-]+\.[a-zA-Z]{2,4}')

for i in range(len(texts)):
  texts[i] = re.sub(email_pattern, '', texts[i])

texts  

["From:  (where's my thing)\nSubject: WHAT car is this!?\nNntp-Posting-Host: rac3.wam.umd.edu\nOrganization: University of Maryland, College Park\nLines: 15\n\n I was wondering if anyone out there could enlighten me on this car I saw\nthe other day. It was a 2-door sports car, looked to be from the late 60s/\nearly 70s. It was called a Bricklin. The doors were really small. In addition,\nthe front bumper was separate from the rest of the body. This is \nall I know. If anyone can tellme a model name, engine specs, years\nof production, where this car is made, history, or whatever info you\nhave on this funky looking car, please e-mail.\n\nThanks,\n- IL\n   ---- brought to you by your neighborhood Lerxst ----\n\n\n\n\n",
 "From:  (Guy Kuo)\nSubject: SI Clock Poll - Final Call\nSummary: Final call for SI clock reports\nKeywords: SI,acceleration,clock,upgrade\nArticle-I.D.: shelley.1qvfo9INNc3s\nOrganization: University of Washington\nLines: 11\nNNTP-Posting-Host: carson.u.washington.edu\n

In [6]:
# Mengubah karakter menjadi lower case
for i in range(len(texts)):
  texts[i] = texts[i].lower()

# Menghilangkan karakter tidak jelas
for i in range(len(texts)):
  texts[i] = re.sub(r"[-()\"#/@;:<>{}`+=~|.!?,*–']", "", texts[i])
  texts[i] = re.sub(r'\n', ' ', texts[i])

texts

['from  wheres my thing subject what car is this nntppostinghost rac3wamumdedu organization university of maryland college park lines 15   i was wondering if anyone out there could enlighten me on this car i saw the other day it was a 2door sports car looked to be from the late 60s early 70s it was called a bricklin the doors were really small in addition the front bumper was separate from the rest of the body this is  all i know if anyone can tellme a model name engine specs years of production where this car is made history or whatever info you have on this funky looking car please email  thanks  il     brought to you by your neighborhood lerxst      ',
 'from  guy kuo subject si clock poll  final call summary final call for si clock reports keywords siaccelerationclockupgrade articleid shelley1qvfo9innc3s organization university of washington lines 11 nntppostinghost carsonuwashingtonedu  a fair number of brave souls who upgraded their si clock oscillator have shared their experienc

In [7]:
#Membuat TF.IDF Vectorizer
vectorizer = TfidfVectorizer()

In [8]:
#Mengubah text yg sudah dipreprocessing kedalam bentuk TF.IDF
X = vectorizer.fit_transform(texts)

In [9]:
#Mentransform Query Menjadi bentuk Vector TF.IDF
query = "what's wrong with the world?"
query_vec = vectorizer.transform([query])

In [11]:
#Menghitung Cosine Similarity Query terhadap Semua Dokumen Yang ada
results = cosine_similarity(X,query_vec).reshape((-1,))

In [12]:
#Menampilkan 10 Dokumen dengan Hasil Cosine Similarity Terbesar
for i in results.argsort()[-10:][::-1]:
    print( '\nScore Cosine Similarity : ', results[i], '\n', data.iloc[i,0],"--",data.iloc[i,1])


Score Cosine Similarity :  0.1953587521462795 
 From: Eugene.Bigelow@ebay.sun.com (Geno )
Subject: Re: The arrogance of Christians
Reply-To: Eugene.Bigelow@ebay.sun.com
Organization: Sun Microsystems, Inc.
Lines: 40

>If I don't think my belief is right and everyone else's belief is wrong,
>then I don't have a belief. This is simply what belief means.

Unfortunatly, this seems to be how Christians are taught to think when
it comes to their religion. Some take it to the extreme and say that
their religion is the ONLY one and if you don't accept their teachings
then you won't be "saved". It takes quite a bit of arrogance to claim
to know what God thinks/wants. Especially when it's based upon your
interpretation of a book. The logic in the above statement is faulty
in that it assumes two people with differing beliefs can't both be
correct. It's all about perception. No two people are exactly alike.
No two people perceive everything in the same way. I believe that
there is one truth. Call